## Galton Board Simulation 

- test with differnt: 
    - peg shapes
    - segment length 
    - gravity
    - ball weight
    - elasticity
    - friction

- possible distrubtion of balls
    - by theory: normal distribution 
    - bimodal and trimodal distributions are possible due to extreme/unusal combinations of weight, gravity, elasticity, and friction
    
- sources:
    - https://github.com/StanislavPetrovV/Python-Galton-Board- 

import pygame as pg
from random import randrange
import pymunk.pygame_util
pymunk.pygame_util.positive_y_is_up = False
from scipy.interpolate import make_interp_spline
import numpy as np
from PIL import Image
import os



In [ ]:
ball_colors = list(pg.color.THECOLORS.keys())[401:450]

In [ ]:
RES = WIDTH, HEIGHT = 500, 800
FPS = 60

pg.init()
surface = pg.display.set_mode(RES)
clock = pg.time.Clock()
draw_options = pymunk.pygame_util.DrawOptions(surface)

space = pymunk.Space()
space.gravity = 0, 6000
ball_mass, ball_radius = 10, 5
segment_thickness = 3

a, b, c, d = int(WIDTH/50), int(HEIGHT/HEIGHT), int(ball_radius*4), int(HEIGHT/30)
x1, x2, x3, x4 = a, WIDTH // 2 - c, WIDTH // 2 + c, WIDTH - a
y1, y2, y3, y4, y5 = b, HEIGHT // 4 - d, HEIGHT // 4, HEIGHT //3 + 5*b, HEIGHT//1.5 - 3 * b
L1, L2, L3, L4 = (x1, -10), (x1, y1), (x2, y2), (x2, y3)
R1, R2, R3, R4 = (x4, -10), (x4, y1), (x3, y2), (x3, y3)
B1, B2 = (0, HEIGHT), (WIDTH, HEIGHT)
T1, T2 = (0, 0), (WIDTH, 0)



def create_ball(space, color):
    ball_moment = pymunk.moment_for_circle(ball_mass, 0, ball_radius)
    ball_body = pymunk.Body(ball_mass, ball_moment)
    ball_body.position = randrange(x1, x4), randrange(-y1, y1)
    ball_shape = pymunk.Circle(ball_body, ball_radius)
    ball_shape.elasticity = 0.1
    ball_shape.friction = 0.8
    ball_shape.color = pg.color.THECOLORS[color]
    space.add(ball_body, ball_shape)
    return ball_body

def add_new_ball(space):
    color = ball_colors[randrange(len(ball_colors))]
    return create_ball(space, color)

def create_segment(from_, to_, thickness, space, color):
    segment_shape = pymunk.Segment(space.static_body, from_, to_, thickness)
    segment_shape.color = pg.color.THECOLORS[color]
    space.add(segment_shape)


def create_rhombus_peg(x, y, space, color, width=20, height=30):
    #define vertices for a rhombus centered at (0, 0)
    vertices = [(-width / 2, 0), (0, -height / 2), (width / 2, 0), (0, height / 2)]
    
    #move vertices to the peg's position
    vertices = [(vx + x, vy + y) for vx, vy in vertices]

    #create a Poly shape for the rhombus
    rhombus_shape = pymunk.Poly(space.static_body, vertices)
    rhombus_shape.color = pg.color.THECOLORS[color]
    rhombus_shape.elasticity = 0.1
    rhombus_shape.friction = 0.5

    space.add(rhombus_shape)



In [ ]:
num_bins = 8  #adjust as needed
bin_counts = [0] * num_bins
bin_width = WIDTH // num_bins
counted_balls = set()

def update_bins(ball):
    #update the bin count based on the ball's final position
    if ball not in counted_balls and ball.velocity.length < velocity_threshold:
        bin_index = int(ball.position.x // bin_width)
        if 0 <= bin_index < num_bins:
            bin_counts[bin_index] += 1
            counted_balls.add(ball)

def smooth_bins(bin_counts, window_size=7):
    smoothed = []
    for i in range(len(bin_counts)):
        start = max(0, i - window_size // 2)
        end = min(len(bin_counts), i + window_size // 2 + 1)
        smoothed.append(sum(bin_counts[start:end]) / (end - start))
    return smoothed

In [ ]:
center_x = WIDTH // 2

#define rhombus dimensions and desired gap
peg_y, step = y4, 40
num_pegs = WIDTH // step + 2
half_num_pegs = num_pegs // 2
rhombus_height = 30  #example height for rhombus pegs
desired_gap = 10  #desired gap between rows of rhombus pegs

#calculate vertical spacing between rows of pegs
vertical_spacing = rhombus_height + desired_gap

for i in range(8):
    peg_x_start = center_x - (half_num_pegs * step)
    if i % 2 == 1:
        peg_x_start += step // 2  #offset every other row for staggering

    peg_y = y4 + i * vertical_spacing  #ddjust vertical position based on row number

    for j in range(num_pegs):
        peg_x = peg_x_start + j * step
        create_rhombus_peg(peg_x, peg_y, space, 'cornsilk3', height=rhombus_height)
        if i == 7:
            create_segment((peg_x, peg_y + rhombus_height*2), (peg_x, HEIGHT), segment_thickness, space, 'cornsilk2')


#segments
platforms = (L1, L2), (L2, L3), (L3, L4), (R1, R2), (R2, R3), (R3, R4)
for platform in platforms:
    create_segment(*platform, segment_thickness, space, 'cornsilk4')
create_segment(B1, B2, 10, space, 'cornsilk2')
create_segment(T1, B1, 2, space, 'cornsilk2')
create_segment(T2, B2, 2, space, 'cornsilk2')



In [ ]:
platforms

In [ ]:
#balls
balls = [(ball_colors[randrange(len(ball_colors))], 
          create_ball(space, ball_colors[randrange(len(ball_colors))])) for j in range(800)]

#user interaction variables
add_ball = False

#define a small velocity threshold
velocity_threshold = 0.4

desired_max_height = HEIGHT - y5
some_color = (0, 0, 255)  #blue color

#set up frame catcher
capture_interval = 1 / 30  #capture every 1/30th of a second for 30fps GIF
capture_next = pg.time.get_ticks() + capture_interval
frame_count = 0
frame_limit = 50 * 30  #50 seconds at 30fps
frames = []

In [ ]:
while True:
    current_time = pg.time.get_ticks() 
    
    for event in pg.event.get():
        if event.type == pg.QUIT:
            pg.quit()
            exit()
        elif event.type == pg.KEYDOWN:
            if event.key == pg.K_SPACE:
                add_ball = True
    
    surface.fill(pg.Color('ivory'))
    
    #add new ball on key press
    if add_ball:
        balls.append(add_new_ball(space))
        add_ball = False

    for i in pg.event.get():
        if i.type == pg.QUIT:
            exit()

    space.step(1 / FPS)
    space.debug_draw(draw_options)

    # [pg.draw.circle(surface, color, ball.position, ball_radius) for color, ball in balls]
    [pg.draw.circle(surface, color, (int(ball.position[0]), int(ball.position[1])),
                    ball_radius) for color, ball in balls]
    
    #update bins based on balls that have stopped moving
    for color, ball in balls:
        if ball.velocity.length < velocity_threshold:  # Check if the ball has stopped
            update_bins(ball)
    #smooth the bin counts
    smoothed_bins = smooth_bins(bin_counts)

    #calculate and draw the curve
    max_count = max(max(smoothed_bins), 1)
    
    x_points = [i * bin_width + bin_width // 2 for i in range(num_bins)]
    y_points = [HEIGHT - (count / max_count) * (desired_max_height//2) for count in bin_counts]

    #apply spline interpolation
    if len(x_points) > 1 and max_count > 1:
        spline = make_interp_spline(x_points, y_points, k=3)  #k=3 for cubic spline
        x_smooth = np.linspace(x_points[0], x_points[-1], 300)  #300 represents number of points to make between x.min and x.max
        y_smooth = spline(x_smooth)

        smooth_curve_points = list(zip(x_smooth, y_smooth))
        pg.draw.aalines(surface, some_color, False, smooth_curve_points)
    
    if current_time >= capture_next and frame_count < frame_limit:
        pg.image.save(surface, f"frame_{frame_count}.png")
        frames.append(Image.open(f"frame_{frame_count}.png"))
        frame_count += 1
        capture_next = current_time + capture_interval
        
    #check if all balls have stopped
    #all_stopped = all(ball.velocity.length < velocity_threshold for _, ball in balls)
    #if all_stopped:
        #break
    
    if frame_count >= frame_limit:
        break

    pg.display.flip()
    clock.tick(FPS)
        
pg.quit()

In [ ]:
#compile frames into a GIF
frames[0].save('pygame_animation_rhom.gif',
               save_all=True, append_images=frames[1:],
               optimize=False, duration=1000 / 30, loop=0)

#optionally, clean up frame images
for i in range(frame_limit):
    os.remove(f"frame_{i}.png")